In [22]:
from itertools import chain

import numpy as np
from bertviz import model_view
from fastapi import FastAPI, File, UploadFile, Header
from onnxruntime import SessionOptions, InferenceSession, GraphOptimizationLevel
from transformers import AutoTokenizer, AutoModel, BertTokenizer, BertForSequenceClassification, BertConfig
from fastapi.middleware.cors import CORSMiddleware
import re
import json
import mimetypes
import torch
import handle
import info
from collections import OrderedDict
import predict
import document
import utils
from configparser import ConfigParser
model_name = './models/bert-roberta'
tokenizer1 = BertTokenizer.from_pretrained(model_name)
config = BertConfig.from_pretrained(model_name)
config.num_hidden_layers = 2
config.num_labels = 7
config.output_attentions = True
model1 = BertForSequenceClassification.from_pretrained(
    model_name, config=config)


Some weights of the model checkpoint at ./models/bert-roberta were not used when initializing BertForSequenceClassification: ['bert.encoder.layer.10.attention.self.query.bias', 'bert.encoder.layer.4.output.LayerNorm.bias', 'bert.encoder.layer.4.attention.self.key.bias', 'bert.encoder.layer.9.attention.self.key.bias', 'bert.encoder.layer.10.attention.self.key.bias', 'bert.encoder.layer.5.attention.self.query.weight', 'bert.encoder.layer.11.attention.self.query.weight', 'bert.encoder.layer.10.attention.output.LayerNorm.weight', 'bert.encoder.layer.7.output.LayerNorm.weight', 'bert.encoder.layer.8.attention.self.key.weight', 'bert.encoder.layer.5.attention.output.LayerNorm.bias', 'bert.encoder.layer.7.attention.self.query.weight', 'bert.encoder.layer.10.intermediate.dense.weight', 'bert.encoder.layer.3.output.dense.weight', 'bert.encoder.layer.2.output.LayerNorm.weight', 'bert.encoder.layer.11.intermediate.dense.weight', 'bert.encoder.layer.6.output.LayerNorm.weight', 'bert.encoder.layer.

In [23]:
model1.load_state_dict(torch.load(
    'models/Roberta.pt', map_location=torch.device('cpu')), strict=False)
model1.eval()


sentence="我是一名程序员"
encoding = tokenizer1.encode_plus(
        sentence,
        add_special_tokens=True,
        padding='max_length',
        truncation=True,
        max_length=128,
        return_tensors='pt'
    )
input_ids = encoding['input_ids'].squeeze()
attention_mask = encoding['attention_mask'].squeeze()
token_type_ids = encoding['token_type_ids'].squeeze()


In [24]:
with torch.no_grad():
    outputs = model1(input_ids.unsqueeze(
        0), attention_mask=attention_mask.unsqueeze(0),token_type_ids=token_type_ids.unsqueeze(0))
    attention=outputs.attentions
    tokens=tokenizer1.convert_ids_to_tokens(encoding['input_ids'][0])


In [25]:
#此处是语句分类模型的注意力机制的原理图

In [26]:
from bertviz import model_view
model_view(attention, tokens)

<IPython.core.display.Javascript object>

In [27]:
#此处是对应onnx模型的原理图
import netron
onnx_path='models/Roberta.onnx'

netron.start(onnx_path)

Serving 'models/Roberta.onnx' at http://localhost:8080


('localhost', 8080)

In [28]:


tokenizer2 = BertTokenizer.from_pretrained(model_name)
config2 = BertConfig.from_pretrained(model_name)
config2.num_hidden_layers = 2
config2.num_labels = 11
config2.output_attentions = True
model2 = BertForSequenceClassification.from_pretrained(
    model_name, config=config2)
model2.load_state_dict(torch.load(
    'models/Job.pt', map_location=torch.device('cpu')), strict=False)
model2.eval()
sentence="我是一名后端工程师"
encoding = tokenizer2.encode_plus(
        sentence,
        add_special_tokens=True,
        padding='max_length',
        truncation=True,
        max_length=512,
        return_tensors='pt'
    )

input_ids = encoding['input_ids'].squeeze()
attention_mask = encoding['attention_mask'].squeeze()
with torch.no_grad():
    outputs = model2(input_ids.unsqueeze(
        0), attention_mask=attention_mask.unsqueeze(0))
    attention=outputs.attentions
    tokens=tokenizer2.convert_ids_to_tokens(encoding['input_ids'][0])
    logits = outputs.logits
    print(logits)
    

Some weights of the model checkpoint at ./models/bert-roberta were not used when initializing BertForSequenceClassification: ['bert.encoder.layer.10.attention.self.query.bias', 'bert.encoder.layer.4.output.LayerNorm.bias', 'bert.encoder.layer.4.attention.self.key.bias', 'bert.encoder.layer.9.attention.self.key.bias', 'bert.encoder.layer.10.attention.self.key.bias', 'bert.encoder.layer.5.attention.self.query.weight', 'bert.encoder.layer.11.attention.self.query.weight', 'bert.encoder.layer.10.attention.output.LayerNorm.weight', 'bert.encoder.layer.7.output.LayerNorm.weight', 'bert.encoder.layer.8.attention.self.key.weight', 'bert.encoder.layer.5.attention.output.LayerNorm.bias', 'bert.encoder.layer.7.attention.self.query.weight', 'bert.encoder.layer.10.intermediate.dense.weight', 'bert.encoder.layer.3.output.dense.weight', 'bert.encoder.layer.2.output.LayerNorm.weight', 'bert.encoder.layer.11.intermediate.dense.weight', 'bert.encoder.layer.6.output.LayerNorm.weight', 'bert.encoder.layer.

tensor([[ 5.0447,  1.3898,  0.4910, -0.3438, -1.5302, -0.5972, -0.7893, -1.1437,
         -1.3625, -1.6107, -2.1593]])


In [ ]:
#此处是用于岗位分类的模型原理图
model_view(attention, tokens)
onnx_path='models/Job.onnx'

netron.start(onnx_path)